In [7]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from PIL import Image
import requests
from io import BytesIO

size = (50, 50)
num_updates_per_frame = 100
num_initial_frames = 60
num_evolution_frames = 500
num_frames = num_initial_frames + num_evolution_frames
DPI = 100
fps = 60

def preprocess_image(url, size=(150, 150), input = None):
    response = requests.get(url)
    if input == None:
        img = Image.open(BytesIO(response.content)).convert('L')
    else:
        img = Image.open(input).convert('L')
    img = img.resize(size)
    img = img.point(lambda x: 0 if x < 128 else 1, '1')
    img_array = np.array(img).flatten()
    img_array = img_array * 2 - 1
    return img_array

def train_hopfield(patterns):
    N = patterns.shape[1]
    W = np.zeros((N, N))
    for p in patterns:
        W += np.outer(p, p)
    W[np.diag_indices(N)] = 0
    W /= patterns.shape[0]
    return W

def update_state(state, W, num_updates=50):
    N = len(state)
    indices = np.random.choice(N, size=num_updates, replace=False)
    s = np.dot(W[indices, :], state)
    state[indices] = np.where(s >= 0, 1, -1)
    return state

def calculate_energy(state, W):
    return -0.5 * np.dot(state, np.dot(W, state))

state0_url = 'https://raw.githubusercontent.com/MerkulovDaniil/optim/refs/heads/master/assets/Notebooks/fmin_hopfield_0.webp'
state1_url = "https://raw.githubusercontent.com/MerkulovDaniil/optim/refs/heads/master/assets/Notebooks/fmin_hopfield_1.webp"
original_image1 = preprocess_image(state0_url, size=size)
N = size[0] * size[1]
original_image1 = original_image1.reshape(N)
original_image2 = preprocess_image(state1_url, size=size)
N = size[0] * size[1]
original_image2 = original_image2.reshape(N)
patterns = np.array([original_image1, original_image2])
W = train_hopfield(patterns)

urls = [
    'https://i.pinimg.com/originals/74/cb/65/74cb65a7e18541edaa4368c00458da66.jpg',
    'https://d18zd1fdi56ai5.cloudfront.net/5b746m5yag25w0jfcnv4dh7tvkql',
    'https://yt3.googleusercontent.com/ytc/AIdro_mxX9g92fL6yO45vJUYe4BIDRnPICJervMXWHlMr6yTOQ=s900-c-k-c0x00ffffff-no-rj',
    'https://i0.wp.com/celebreligions.com/wp-content/uploads/2017/11/Mark-Zuckerberg-2048x1064.jpg?resize=600%2C600&ssl=1',
    ]

initial_states = []
for url in urls:
    img = preprocess_image(url, size=size)
    initial_states.append(img)

states = [state.copy() for state in initial_states]

fig, axes = plt.subplots(2, 2, figsize=(8, 8), dpi=DPI)
axes = axes.flatten()
plt.subplots_adjust(left=0.05, right=0.95, top=0.95, bottom=0.05, wspace=0.02, hspace=0.02)

ims = []
energy_texts = []
for i in range(4):
    im = axes[i].imshow(states[i].reshape(size), cmap='gray', animated=True)
    axes[i].axis('off')
    ims.append(im)
    energy_text = axes[i].text(0.5, 0.0, '', ha='center', va='top', transform=axes[i].transAxes, fontsize=8, color='blue')
    energy_texts.append(energy_text)

def init():
    for i in range(4):
        ims[i].set_array(states[i].reshape(size))
        energy_texts[i].set_text('')
    return ims + energy_texts

def animate(frame):
    if frame < num_initial_frames:
        for i in range(4):
            ims[i].set_array(initial_states[i].reshape(size))
            energy = calculate_energy(initial_states[i], W)
            energy_texts[i].set_text(f'Energy: {energy}')
    else:
        for i in range(4):
            states[i] = update_state(states[i], W, num_updates=num_updates_per_frame)
            ims[i].set_array(states[i].reshape(size))
            energy = calculate_energy(states[i], W)
            energy_texts[i].set_text(f'Energy: {energy}')
    return ims + energy_texts

ani = animation.FuncAnimation(fig, animate, init_func=init, frames=num_frames, 
                              blit=True, interval=1/fps*1000)
plt.close()
# ani.save('fmin_nobel_energy.mp4', writer='ffmpeg', fps=fps)
from IPython.display import HTML
HTML(ani.to_html5_video())

In [6]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from PIL import Image
import requests
from io import BytesIO

size = (250, 250)
num_updates_per_frame = 1000
num_initial_frames = 120
num_evolution_frames = 600
num_frames = num_initial_frames + num_evolution_frames
DPI = 300
fps=60

def preprocess_image(url, size=(150, 150), input = None):
    if input == None:
        response = requests.get(url)
        img = Image.open(BytesIO(response.content)).convert('L')  # Convert to grayscale
    else:
        img = Image.open(input).convert('L')
    img = img.resize(size)
    img = img.point(lambda x: 0 if x < 128 else 1, '1')  # Convert to binary
    img_array = np.array(img).flatten()
    img_array = img_array * 2 - 1  # Convert to -1 and 1
    return img_array

def train_hopfield(patterns):
    N = patterns.shape[1]
    W = np.zeros((N, N))
    for p in patterns:
        W += np.outer(p, p)
    W[np.diag_indices(N)] = 0  # No self-connections
    W /= patterns.shape[0]
    return W

def update_state(state, W, num_updates=50):
    N = len(state)
    indices = np.random.choice(N, size=num_updates, replace=False)
    
    # Vectorized computation for selected indices
    s = np.dot(W[indices, :], state)  # Matrix-vector multiplication for selected rows
    state[indices] = np.where(s >= 0, 1, -1)  # Update the state based on the sign of the result
    
    return state

state0_url = 'https://raw.githubusercontent.com/MerkulovDaniil/optim/refs/heads/master/assets/Notebooks/fmin_hopfield_0.webp'
state1_url = "https://raw.githubusercontent.com/MerkulovDaniil/optim/refs/heads/master/assets/Notebooks/fmin_hopfield_1.webp"
original_image1 = preprocess_image(state0_url, size=size)
N = size[0] * size[1]
original_image1 = original_image1.reshape(N)
original_image2 = preprocess_image(state1_url, size=size)
N = size[0] * size[1]
original_image2 = original_image2.reshape(N)
patterns = np.array([original_image1, original_image2])
W = train_hopfield(patterns)

urls = [
    'https://i.pinimg.com/originals/74/cb/65/74cb65a7e18541edaa4368c00458da66.jpg',
    'https://d18zd1fdi56ai5.cloudfront.net/5b746m5yag25w0jfcnv4dh7tvkql',
    'https://yt3.googleusercontent.com/ytc/AIdro_mxX9g92fL6yO45vJUYe4BIDRnPICJervMXWHlMr6yTOQ=s900-c-k-c0x00ffffff-no-rj',
    # 'https://yt3.googleusercontent.com/ytc/AGIKgqMHhWshXIxWeQUhrp_QIy0ouw-QBIE9xzCQ6QRBUw=s900-c-k-c0x00ffffff-no-rj',
    'https://i0.wp.com/celebreligions.com/wp-content/uploads/2017/11/Mark-Zuckerberg-2048x1064.jpg?resize=600%2C600&ssl=1',
    # 'https://images.lifestyleasia.com/wp-content/uploads/sites/6/2023/04/18161022/elon-musk-ai-compant-1.jpeg',
    ]

initial_states = []
for url in urls:
    print(url)
    img = preprocess_image(url, size=size)
    initial_states.append(img)

states = [state.copy() for state in initial_states]

fig, axes = plt.subplots(2, 2, figsize=(8, 8), dpi=DPI)
axes = axes.flatten()

# Adjusting the layout to have a small margin between subplots and minimal margins around the figure
plt.subplots_adjust(left=0.05, right=0.95, top=0.95, bottom=0.05, wspace=0.02, hspace=0.02)
axes[-1].annotate('@fminxyz',
                fontsize=16, c='grey', zorder=20,
                xy=(1, -0.02), xytext=(0, 20),
                xycoords=('axes fraction', 'figure fraction'),
                textcoords='offset points',
                ha='right', va='bottom')

ims = []
for i in range(4):
    im = axes[i].imshow(states[i].reshape(size), cmap='gray', animated=True)
    axes[i].axis('off')
    ims.append(im)

def init():
    for i in range(4):
        ims[i].set_array(states[i].reshape(size))
    return ims

def animate(frame):
    if frame < num_initial_frames:
        # During the initial frames, we display the original initial states without updating
        for i in range(4):
            ims[i].set_array(initial_states[i].reshape(size))
    else:
        # After the initial frames, update and animate
        for i in range(4):
            states[i] = update_state(states[i], W, num_updates=num_updates_per_frame)
            ims[i].set_array(states[i].reshape(size))
    return ims

ani = animation.FuncAnimation(fig, animate, init_func=init, frames=num_frames, 
                              blit=True, interval=1/fps*1000)
plt.close()
# ani.save('fmin_nobel.mp4', writer='ffmpeg', fps=fps)
from IPython.display import HTML
HTML(ani.to_html5_video())

https://i.pinimg.com/originals/74/cb/65/74cb65a7e18541edaa4368c00458da66.jpg
https://d18zd1fdi56ai5.cloudfront.net/5b746m5yag25w0jfcnv4dh7tvkql
https://yt3.googleusercontent.com/ytc/AIdro_mxX9g92fL6yO45vJUYe4BIDRnPICJervMXWHlMr6yTOQ=s900-c-k-c0x00ffffff-no-rj
https://i0.wp.com/celebreligions.com/wp-content/uploads/2017/11/Mark-Zuckerberg-2048x1064.jpg?resize=600%2C600&ssl=1
